In [1]:
from gensim.models import KeyedVectors
from gensim.models.doc2vec import TaggedDocument, Doc2Vec

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import StratifiedShuffleSplit
from sklearn.naive_bayes import MultinomialNB
from sklearn.pipeline import Pipeline
from sklearn.svm import LinearSVC
from sklearn.svm import SVC
from sklearn.multiclass import OneVsRestClassifier
from sklearn.metrics import classification_report
from sklearn.preprocessing import FunctionTransformer, MultiLabelBinarizer

from nltk import sent_tokenize
from nltk import pos_tag
from nltk import map_tag
from nltk import word_tokenize
from nltk.corpus import stopwords

import pandas as pd
import numpy as np
import torch
import json
import re
import csv
from tqdm import tqdm

In [2]:
metadata = pd.read_csv("../data/movie.metadata.tsv", sep = '\t', header = None)
metadata.columns = ["movie_id",1,"movie_name",3,4,5,6,7,"genre"]

plots = []
with open("../data/plot_summaries.txt", 'r') as f:
    reader = csv.reader(f, dialect='excel-tab') 
    for row in tqdm(reader):
        plots.append(row)

movie_id = []
plot = []

# extract movie Ids and plot summaries
for i in tqdm(plots):
    movie_id.append(i[0])
    plot.append(i[1])

# create dataframe
movies = pd.DataFrame({'movie_id': movie_id, 'plot': plot})

# change datatype of 'movie_id'
metadata['movie_id'] = metadata['movie_id'].astype(str)

# merge meta with movies
movies = pd.merge(movies, metadata[['movie_id', 'movie_name', 'genre']], on = 'movie_id')

genres = [] 

# extract genres
for i in movies['genre']: 
    genres.append(list(json.loads(i).values())) 

# add to 'movies' dataframe  
movies['genre_new'] = genres

movies_new = movies[~(movies['genre_new'].str.len() == 0)]

def clean_text(text):
    # remove a string like {{plot}}
    text = re.sub("\s*{{\w*}}\s*", "", text)
    # remove backslash-apostrophe 
    text = re.sub("\'", "", text)
    
    text = text.lower().replace('\n', ' ').replace('\t', ' ').replace('\xa0',' ') #get rid of problem chars
    
    text = ' '.join(text.split())
    
    return text

movies_new['clean_plot'] = movies_new['plot'].apply(lambda x: clean_text(x))

42303it [00:01, 37036.26it/s]
100%|██████████| 42303/42303 [00:00<00:00, 1193620.20it/s]
/anaconda3/envs/workspace/lib/python3.7/site-packages/ipykernel_launcher.py:50: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [24]:
def doc2vec(data_df):
    data = []
    print("Building TaggedDocuments")
    total = len(data_df[['movie_id', 'clean_plot']].as_matrix().tolist())
    processed = 0
    for x in data_df[['movie_id', 'clean_plot']].as_matrix().tolist():
        label = ["_".join(x[0].split())]
        words = []
        sentences = sent_tokenize(x[1])
        for s in sentences:
            words.extend([x for x in word_tokenize(s)])
        doc = TaggedDocument(words, label)
        data.append(doc)

        processed += 1
        if processed % 10000 == 0:
            print(processed, "/", total)

    model = Doc2Vec(min_count=1, window=10, size=300, sample=1e-5, negative=5, workers=2, epochs=20, min_alpha=0.00025)
    
    print("Building Vocabulary")
    model.build_vocab(data)
    
    print("Training starts")
    
    model.train(documents=data, total_examples=model.corpus_count, epochs=model.epochs)
    
    # Build doc2vec vectors
    x_data = []
    genres = data_df['genre_new'].as_matrix().tolist()
    binarizer = MultiLabelBinarizer()
    y_data = binarizer.fit_transform(genres)
    ids = data_df[['movie_id']].as_matrix().tolist()
    for i in range(len(ids)):
        movie_id = ids[i][0]
        label = "_".join(movie_id.split())
        x_data.append(model.docvecs[label])

    return np.array(x_data), y_data


In [25]:
x_data, y_data = doc2vec(movies_new)

Building TaggedDocuments
TaggedDocument(['shlykov', ',', 'a', 'hard-working', 'taxi', 'driver', 'and', 'lyosha', ',', 'a', 'saxophonist', ',', 'develop', 'a', 'bizarre', 'love-hate', 'relationship', ',', 'and', 'despite', 'their', 'prejudices', ',', 'realize', 'they', 'arent', 'so', 'different', 'after', 'all', '.'], ['23890098'])
TaggedDocument(['the', 'nation', 'of', 'panem', 'consists', 'of', 'a', 'wealthy', 'capitol', 'and', 'twelve', 'poorer', 'districts', '.', 'as', 'punishment', 'for', 'a', 'past', 'rebellion', ',', 'each', 'district', 'must', 'provide', 'a', 'boy', 'and', 'girl', 'between', 'the', 'ages', 'of', '12', 'and', '18', 'selected', 'by', 'lottery', 'for', 'the', 'annual', 'hunger', 'games', '.', 'the', 'tributes', 'must', 'fight', 'to', 'the', 'death', 'in', 'an', 'arena', ';', 'the', 'sole', 'survivor', 'is', 'rewarded', 'with', 'fame', 'and', 'wealth', '.', 'in', 'her', 'first', 'reaping', ',', '12-year-old', 'primrose', 'everdeen', 'is', 'chosen', 'from', 'district

/anaconda3/envs/workspace/lib/python3.7/site-packages/ipykernel_launcher.py:4: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  after removing the cwd from sys.path.
/anaconda3/envs/workspace/lib/python3.7/site-packages/ipykernel_launcher.py:6: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  


TaggedDocument(['the', 'film', 'begins', 'with', 'a', 'boy', 'named', 'michael', ',', 'a', 'kid', 'who', 'has', 'the', 'hots', 'for', 'a', 'beautiful', 'girl', 'named', 'jada', ',', 'but', 'is', 'always', 'rejected', 'because', 'jada', 'is', 'stuck', 'with', 'a', 'gangster', ',', 'lorenzo', ',', 'and', 'when', 'michael', 'comes', 'close', 'to', 'her', ',', 'he', 'is', 'threatened', 'with', 'bodily', 'harm', 'by', 'getting', 'beat', 'up', 'by', 'both', 'lorenzo', 'and', 'his', 'homeboys', ',', 't-bone', 'and', 'baby', 'boy', '.', 'but', 'michael', 'is', 'secretly', 'involved', 'in', 'black', 'magic', ',', 'and', 'tries', 'to', 'bring', 'a', 'doll', 'that', 'he', 'keeps', 'calling', 'killjoy', 'to', 'life', '.', 'but', 'the', 'spell', 'does', 'not', 'work', 'quickly', ';', 'after', 'he', 'is', 'abducted', 'by', 'the', 'gangsters', 'and', 'brought', 'into', 'an', 'abandoned', 'area', 'of', 'the', 'woods', ',', 'michael', 'is', 'accidentally', 'shot', 'and', 'killed', 'by', 'lorenzo', 'whe

TaggedDocument(['phir', 'kabhi', 'targets', 'the', 'heart', 'of', 'its', 'audience', '.', 'it', 'is', 'all', 'about', 'emotions', '.', 'it', 'is', 'a', 'sensitive', 'tale', 'of', 'love', '.', 'there', 'are', 'many', 'moments', 'in', 'the', 'film', 'where', 'one', 'may', 'realize', 'the', 'meaning', 'behind', 'the', 'saying', ',', 'crying', 'while', 'laughing', 'and', 'laughing', 'also', 'while', 'crying', '.', 'how', 'both', 'the', 'phenomena', 'happen', 'together', 'can', 'be', 'witnessed', 'via', 'few', 'moments', 'of', 'this', 'film', '.', 'film', 'rides', 'over', 'the', 'successive', 'sequences', 'of', 'light', 'and', 'sensitive', 'scenes', '.', 'at', 'one', 'moment', 'something', 'light', ',', 'humorous', 'and', 'lively', 'is', 'happening', 'on', 'screen', 'and', 'a', 'smile', 'is', 'flowing', 'on', 'the', 'lips', 'of', 'the', 'characters', 'and', 'audiences', 'also', 'and', 'all', 'of', 'a', 'sudden', 'it', '’', 's', 'followed', 'by', 'a', 'very', 'intense', 'and', 'sensitive', '

TaggedDocument(['two', 'elderly', 'ladies', '(', 'one', 'of', 'which', 'is', '[', '[', 'granny', ',', 'the', 'owners', 'of', 'sylvester', 'and', 'tweety', ',', 'sneak', 'their', 'pets', 'into', 'a', 'hotel', 'where', 'no', 'pets', 'are', 'allowed', '.', 'sylvester', ',', 'hearing', 'tweetys', 'singing', 'in', 'the', 'room', 'next', 'to', 'his', ',', 'writes', 'a', 'letter', 'to', 'the', 'canary', 'from', 'his', '``', 'ardent', 'admirer', "''", '.', 'tweety', 'shortly', 'discovers', 'who', 'his', '``', 'admirer', "''", 'is', ',', 'and', 'a', 'chase', 'ensues', ',', 'which', 'is', 'cut', 'short', 'by', 'the', 'doorman', ',', 'forcing', 'sylvester', 'to', 'disguise', 'himself', 'causing', 'the', 'doorman', 'to', 'apologize', 'and', 'flee', '.', 'sylvester', 'then', 'sneaks', 'into', 'tweetys', 'room', 'and', 'tries', 'to', 'get', 'him', 'in', 'his', 'cage', ';', 'this', 'backfires', 'and', 'he', 'is', 'knocked', 'out', 'by', 'the', 'spring-loaded', 'cage', '.', 'sylvester', 'then', 'phone

...

TaggedDocument(['the', 'film', 'begins', 'with', 'navin', 'r.', 'johnson', ',', 'a', 'homeless', 'bum', ',', 'directly', 'addressing', 'the', 'camera', 'and', 'telling', 'his', 'story', '.', 'he', 'is', 'the', 'adopted', 'white', 'son', 'of', 'african', 'american', 'sharecroppers', ',', 'who', 'grows', 'to', 'adulthood', 'naïvely', 'unaware', 'of', 'his', 'obvious', 'adoption', '.', 'he', 'stands', 'out', 'in', 'his', 'family', 'not', 'just', 'because', 'of', 'his', 'skin', 'color', ',', 'but', 'also', 'because', 'of', 'his', 'utter', 'lack', 'of', 'rhythm', 'when', 'his', 'adopted', 'family', 'plays', 'spirited', 'blues', 'music', '.', 'one', 'night', ',', 'he', 'hears', 'the', 'staid', 'and', 'starchy', 'roger', 'wolfe', 'kahn', 'orchestra', 'song', 'called', '``', 'crazy', 'rhythm', "''", 'on', 'the', 'radio', 'and', 'his', 'feet', 'spontaneously', 'begin', 'to', 'move', 'with', 'the', 'urge', 'to', 'dance', ';', 'he', 'sees', 'this', 'as', 'a', 'calling', 'and', 'decides', 'to', 'h

TaggedDocument(['the', 'film', 'opens', 'on', 'a', 'long', 'strand', 'of', 'beach', ',', 'where', 'several', 'people', 'in', 'white', 'robes', 'gather', 'around', 'a', 'young', 'man', 'named', 'ilius', ',', 'adorning', 'him', 'in', 'a', 'vest', 'of', 'leather', 'armor', ',', 'while', 'an', 'old', 'man', 'hands', 'him', 'a', 'bow', 'and', 'a', 'set', 'of', 'arrows', ',', 'summoning', 'it', 'to', 'fly', 'to', 'them', '.', 'the', 'old', 'man', 'tells', 'ilius', 'the', 'tale', 'of', 'an', 'ancient', 'warrior', 'god', 'named', 'kronos', ',', 'who', 'once', 'wielded', 'the', 'bow', ',', 'and', 'how', 'when', 'he', 'ran', 'out', 'of', 'arrows', ',', 'the', 'sun', 'itself', 'seemed', 'to', 'vanish', 'from', 'the', 'sky', ',', 'transferring', 'itself', 'to', 'his', 'bow', ',', 'making', 'arrows', 'out', 'of', 'pure', 'sunlight', '.', 'after', 'telling', 'ilius', 'this', 'tale', ',', 'the', 'old', 'man', 'and', 'his', 'people', 'depart', 'as', 'ilius', 'wordlessly', 'departs', 'down', 'the', 'be

TaggedDocument(['benjamin', 'jahrvi', 'has', 'moved', 'to', 'new', 'york', 'city', 'where', 'he', 'is', 'selling', 'toy', 'versions', 'of', 'johnny', '5', 'on', 'the', 'street', '.', 'struggling', 'department', 'store', 'buyer', 'sandy', 'banatoni', 'sees', 'the', 'toys', 'and', 'orders', '1,000', 'units', '.', 'ben', 'is', 'helped', 'by', 'con', 'artist', 'fred', 'ritter', 'with', 'the', 'project', '.', 'fred', 'borrows', 'money', 'from', 'a', 'loan', 'shark', 'for', 'equipment', ',', 'hires', 'temporary', 'workers', 'and', 'rents', 'a', 'warehouse', 'to', 'build', 'the', 'toys', '.', 'unfortunately', ',', 'the', 'warehouse', 'is', 'the', 'base', 'of', 'operations', 'for', 'a', 'couple', 'of', 'thieves', 'hired', 'by', 'bank', 'teller', 'oscar', 'baldwin', 'to', 'tunnel', 'into', 'the', 'bank', 'vault', 'across', 'the', 'street', '.', 'they', 'plan', 'to', 'steal', 'a', 'set', 'of', 'jewels', 'known', 'as', 'the', 'vanderveer', 'collection', ',', 'worth', '$', '37,862,000', '.', 'the'

TaggedDocument(['the', 'film', 'begins', 'in', 'a', 'bowling', 'alley', ',', 'where', 'a', 'group', 'of', 'friends', 'are', 'awaiting', 'the', 'arrival', 'of', 'salim', '.', 'meanwhile', ',', 'deepak', 'arrives', 'with', 'his', 'fiancée', 'sheetal', '.', 'when', 'a', 'conversation', 'about', 'love', 'arises', ',', 'deepak', 'and', 'the', 'rest', 'find', 'it', 'necessary', 'to', 'make', 'sheetal', 'aware', 'that', 'true', 'love', 'does', 'exist', '.', 'they', 'tell', 'her', 'the', 'story', 'of', 'raj', 'and', 'priya', ',', 'two', 'of', 'their', 'closest', 'friends', '.', 'raj', 'mathur', 'is', 'the', 'owner', 'of', 'raj', 'transport', ',', 'a', 'small', 'trucking', 'company', 'he', 'founded', 'himself', '.', 'raj', 'is', 'a', 'carefree', 'man', 'who', 'is', 'unorganized', ',', 'messy', ',', 'lazy', 'and', 'late', 'all', 'the', 'time', '.', 'although', 'he', 'isnt', 'the', 'richest', ',', 'hes', 'always', 'happy', '.', 'on', 'the', 'other', 'hand', ',', 'priya', 'chopra', 'is', 'a', 'suc

KeyboardInterrupt: 

In [18]:
import pickle 
with open('doc2vec_data.pkl', 'wb') as f:
    pickle.dump((x_data, y_data), f)

In [19]:
with open('doc2vec_data.pkl', 'rb') as f:
    data = pickle.load(f)
    x_data, y_data = data[0], data[1]